## Testing sequence reconstruction (varying L, delta) for Bidirectional beam search

Bidirectional beam search - https://github.com/GZHoffie/bbs

Varying L, delta for capping and no capping. Bernoulli trials for adding bases, failure - capping goes to the next strand, no capping continues with a deletion error. Running through Badread as the Nanopore error simulator

In [37]:
from synthesis import NaiveSynthesisModel
import numpy as np
from utils import create_fasta_file
from uuid import uuid4

In [38]:

coupling_rates = np.arange(0.90, 1.0, 0.01)
lengths = [200]
synthesis_models = []
repeats = 500

for coupling_rate in coupling_rates:
    for length in lengths:
        #capped = NaiveSynthesisModel(coupling_rate=coupling_rate, strand_length=length, capping=True, repeats=repeats)
        no_capped = NaiveSynthesisModel(coupling_rate=coupling_rate, strand_length=length, capping=False, repeats=repeats) 
        
        synthesis_models.extend([capped, no_capped])

In [39]:
strands = []

for synth_model in synthesis_models:
    strands_ = synth_model.simulate_synthesis()
    if synth_model.capping:
        strands_ = [i for i in strands_ if len(strands_) == synth_model.strand_length]  # Filtering out incomplete capping strands
    strands.extend(strands_)

In [40]:
ids = [uuid4() for i in range(len(strands))]

In [41]:
# Writing strands to fasta for badread

create_fasta_file(ids, strands, "bbs_0.9_1_50_200.fasta")

File saved as bbs_0.9_1_50_200.fasta


### Coupling rate 0.9 - 1 (length 200) - no capping

1. Read fq
2. Cluster
3. Write for BBS
4. Check results

In [45]:
from utils import get_fastq_records

In [46]:
sequenced_strands = get_fastq_records(fastq_filepath=r"C:\Users\Parv\Doc\RA\Projects\clustering_dna_storage\reads.fastq\reads.fastq")

19354it [00:00, 21013.26it/s]


In [51]:
sequenced_strands[0]

SeqRecord(seq=Seq('GCATTCCACACCAAGATGAATACAGCATAACAAACCAAAATCTCTGCTAGCGCT...GCC'), id='f9cc19b1-2954-8e70-a280-9e162cf60d57', name='f9cc19b1-2954-8e70-a280-9e162cf60d57', description='f9cc19b1-2954-8e70-a280-9e162cf60d57 614e30fa-5e61-4240-a548-3f82a8909485,+strand,0-188 length=187 error-free_length=188 read_identity=96.078%', dbxrefs=[])

In [73]:
s.clustered_seqs[2]

['...',
 ...]

In [74]:
dict_ = {f"cluster_{i}": s.clustered_seqs[i] for i in range(len(s.clustered_seqs))}

In [76]:
import json

with open("bbs_clusters.json", "w") as f:
    json.dump(dict_, f)

In [52]:
sequenced_strands_ = [str(i.seq) for i in sequenced_strands]

In [79]:

with open("bbs_clusters.json", "r") as f:
    clusters = json.load(f)

In [80]:
clusters

{'cluster_0': ['...',
  ...],
 'cluster_1': ['...',
  ...],
 'cluster_2': ['...',
  ...],
 'cluster_3': ['...',
  ...],
 'cluster_4': ['...',
  ...],
 'cluster_5': ['...',
  ...],
 'cluster_6': ['...',
  ...],
 'cluster_7': ['...',
  ...],
 'cluster_8': ['...',
  ...],
 'cluster_9': ['...',
  ...],
 'cluster_10': ['...'],
 'cluster_11': ['TCACTATTCGGTCAGACTCGTAACTCTTAGACGCGTGGATAGTAGCCCTATACTGTAGTCGAATCCAAGTGTAGCGCTTCCGTCTATCATACTCATTGGACCAGCCAAGGGGAGCTTGTCCGTTGTATGGCGCAGGAAGGAGAAAAGTATAAGCCGATGTTATTTATCTTGTACATC',
  'TCACTATTCGGGTCAGACTCGAACTCTTAGACGCGTGGGTAGTAGCCCTATACTGTAGTCGAATTGAAGTGTAGCGCTTCCGTCTATCATACTCATTGGACCAAGCCAAGGGGAGCTTGTCGTTGTATGGCGCAGGAAGGAGAAAAGTATAAGCCGATGTTATTTATCTGTACATC',
  'TCACTATTCCGGGTCAACTCTAACTCTATAGACGCAGTTAAGGTAGCACCCTACTGTAGTCGAATCCAACGTGTAGCGCTTCCCGTTATATCTCAAATTGCACCAGCCAAGGGGATTGCGTGTGATGGCCGCAGGAAGAGAAAAGTATAGCGTGTTGATTTAGCTGTCAGTC',
  'TCACTATTCCGGGTCAGACTCGAACTGCTATGACGCATAGTAAGCACCCTATACTTGTCGATCAACGTGTAGCGCTTGCCGTCTTTCATCATCGATTGGCACAGCCAAGGGGAGTT

In [53]:
from clustering import Clustering

In [54]:
s = Clustering(sequenced_strands_, reference_length=200)

In [55]:
s.run_pipeline()

Clustering strands
Total strands 19354


100%|██████████| 19354/19354 [24:13<00:00, 13.31it/s] 


Number of clusters = 816
Clusters are sorted
Orientation fixed in the strand pool
Generating 100 candidates


100%|██████████| 100/100 [00:10<00:00,  9.35it/s]


In [56]:
s.candidates

['TCAACTAATAGCTACATGGCTTTAGGTCGTGTCCCTGGTTGGTTTCCCGAACTCCCCATTGGCGGCTTAATCTGCGCTTGTGCAGAGGCTGAGTTATTTTACTGTATCCACTGGCCTGCTGGTATCCCGCTCTATGTTCTCCTCATTACGGAATTCTTCGTTAAGCGAAGACTCCTAAGTATGAACGGTTAG',
 'GCGTATTACCACACCGAGAATGAATACAGCATGACAAACAAAATCTCGCTAGCGCTGAAAACCCGAGACAGACTAGACTAACGCTCAGAAGCCGTCAACCCACGCGCAGCTAGGAGGGCCTCGGTATGGGTCGATCATCGGCCCGTTCATTTAGCACGTAGTCGACAGACAATTCAATGCGGACTCTCCAACACGCC',
 'CTGCTTGCACTAAAAGCCCGTATGTTGCGCAGGGACCGTGCACAACGAAGTAGACGGAGCATAACACTAGGCGTTGGAGATCGTCCGAGCCACTATTAAAGGTGGACTCTATTCGGTACAAAGACTGAGGCATTGTGGGCTTCGGGGCGTGGATGAGCCTTGAGGCGGTCCAAGATGTCTGCGAGAGTAGATTAGCTTAC',
 'AGTGCACTGTCTCCTCTTAAGACCCGGGATGGCCAAAAGGTTTTGACTAACTCACGAGGCTGATTACCACATACTAGAAGAGGCGCCTCAGCAACATACCTGGCAGGAAATCTGAAGAAAATCTTAACGGCAAAGCATTCAGTCTGTCCTCGTCGGGAAGCAGAGCTCCCGTGACGGCGTTCAAGCTGCGCCTGCAGTGG',
 'GGTCTTACCTAGACTGCAATTCTCTTACAGACAGAATGATGGTACGAGGGATACCAACCTGGTCACGGGCGGTTCTAAGTGCCAACATCATATAGCATCCGATAAATCTAGTTTGCTCCTAGGTGTTGACAGGGGTCACGATCACTATAAATGTCTCTGTATCCCTCAATTAACCAGCTTTTCTCCACC

In [58]:
references = [i.strand for i in synthesis_models]

In [60]:
len(references)

20

In [62]:
from Levenshtein import distance
from utils import reverse_complement

In [64]:

indices = []
min_distances = []

for i in s.candidates:
    rev_i = reverse_complement(i)
    min_distance = 200
    index = 0
    for ptr, j in enumerate(references):

        dis1 = distance(i, j)
        dis2 = distance(rev_i, j)

        if dis1 < min_distance:
            index = ptr
            min_distance = dis1
        
        
        if dis2 < min_distance:
            index = ptr
            min_distance = dis2

    indices.append(index)
    min_distances.append(min_distance)

In [67]:
for ptr, indice in enumerate(indices):
    min_distance = min_distances[ptr]
    reference_cr = synthesis_models[ptr].coupling_rate

    print(f"Minimum distance {min_distance}, Coupling rate {reference_cr}")

Minimum distance 8, Coupling rate 0.9900000000000001
Minimum distance 3, Coupling rate 0.9
Minimum distance 0, Coupling rate 0.9900000000000001
Minimum distance 0, Coupling rate 0.91
Minimum distance 0, Coupling rate 0.9900000000000001
Minimum distance 0, Coupling rate 0.92
Minimum distance 3, Coupling rate 0.9900000000000001
Minimum distance 2, Coupling rate 0.93
Minimum distance 9, Coupling rate 0.9900000000000001
Minimum distance 12, Coupling rate 0.9400000000000001
Minimum distance 15, Coupling rate 0.9900000000000001
Minimum distance 15, Coupling rate 0.9500000000000001
Minimum distance 8, Coupling rate 0.9900000000000001
Minimum distance 17, Coupling rate 0.9600000000000001
Minimum distance 16, Coupling rate 0.9900000000000001
Minimum distance 21, Coupling rate 0.9700000000000001
Minimum distance 166, Coupling rate 0.9900000000000001
Minimum distance 17, Coupling rate 0.9800000000000001
Minimum distance 135, Coupling rate 0.9900000000000001
Minimum distance 27, Coupling rate 0.99

IndexError: list index out of range